In [1]:
import benepar
from IPython.core.debugger import set_trace
import os

parser = benepar.Parser("benepar_en2_large")

save_dir = "ancestor_information_analysis"
if not os.path.exists(save_dir):
    os.mkdir(save_dir)

In [2]:
hp_text = open("chapter9.txt","r").readlines()
all_text = []
para = ""
for i in range(len(hp_text)):
    hp_text[i] = hp_text[i].strip()
    if hp_text[i]!="+":
        para += hp_text[i] + " "
    else:
        all_text.append(para)
        para = ""

In [3]:
def return_all_leaf_paths(tree):
    if isinstance(tree[0], str): # we are at a leaf
        return [[tree.label(),tree[0]]]
    all_paths = []
    for subtree in tree:
        all_paths += return_all_leaf_paths(subtree)
    for i in range(len(all_paths)):
        all_paths[i] = [tree.label()] + all_paths[i]
    return all_paths

In [4]:
all_paths = []
for i in range(len(hp_text)):
    all_paths.append([])
    
tree_end_points = [0]

ptr = 0
len_remaining = len(hp_text[ptr])
for para in all_text:
    trees = parser.parse_sents(para)
    for tree in trees:
        all_paths_to_leaves = return_all_leaf_paths(tree)
        for path in all_paths_to_leaves:
            if path[-1] == "``" or path[-1] == "''" or path[-1] == "-LRB-" or path[-1] == "-RRB-":
                len_remaining -= 1
            else:
                len_remaining -= len(path[-1])
            all_paths[ptr].append(path)
            if len_remaining == 0:
                ptr += 1
                while(ptr != len(hp_text) and hp_text[ptr] == "+"):
                    ptr += 1
                if ptr != len(hp_text):
                    len_remaining = len(hp_text[ptr])
        tree_end_points.append(ptr)

In [5]:
max_path_len = 0
tag_to_idx = {}
idx_to_tag = {}
idx = 0
for p in all_paths:
    for q in p:
        for t in q[:-1]:
            if t not in tag_to_idx:
                tag_to_idx[t] = idx
                idx_to_tag[idx] = t
                idx += 1
        if len(q) > max_path_len:
            max_path_len = len(q)

In [6]:
levels = []
for i in range(len(hp_text)):
    levels.append([])
    for j in range(max_path_len):
        levels[i].append([0]*len(tag_to_idx))

In [7]:
for i in range(len(tree_end_points)-1):
    sent_start = tree_end_points[i]
    sent_end = tree_end_points[i+1]
    all_paths_in_this_tree = []
    iters = []
    path_to_word = {}
    cnt = 0
    for j in range(sent_start,sent_end):
        all_paths_in_this_tree += all_paths[j]
        while(cnt < len(all_paths_in_this_tree)):
            path_to_word[cnt] = j
            cnt += 1
    for j in range(len(all_paths_in_this_tree)):
        iters.append(len(all_paths_in_this_tree[j])-2)
    level_num = 0
    while(max(iters) != -1):
        maxi = max(iters)
        for j in range(len(iters)):
            levels[path_to_word[j]][level_num][tag_to_idx[all_paths_in_this_tree[j][iters[j]]]] = 1
            if iters[j] == maxi:
                iters[j] -= 1
        level_num += 1

In [8]:
for i in range(len(hp_text)):
    print(hp_text[i])
    print(all_paths[i])

Harry
[['S', 'S', 'NP', 'NNP', 'Harry']]
had
[['S', 'S', 'VP', 'VBD', 'had']]
never
[['S', 'S', 'VP', 'ADVP', 'RB', 'never']]
believed
[['S', 'S', 'VP', 'VP', 'VBN', 'believed']]
he
[['S', 'S', 'VP', 'VP', 'SBAR', 'S', 'NP', 'PRP', 'he']]
would
[['S', 'S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'MD', 'would']]
meet
[['S', 'S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'VP', 'VB', 'meet']]
a
[['S', 'S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'VP', 'NP', 'NP', 'DT', 'a']]
boy
[['S', 'S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'VP', 'NP', 'NP', 'NN', 'boy']]
he
[['S', 'S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'VP', 'NP', 'SBAR', 'S', 'NP', 'PRP', 'he']]
hated
[['S', 'S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'VP', 'NP', 'SBAR', 'S', 'VP', 'VBD', 'hated']]
more
[['S', 'S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'VP', 'NP', 'SBAR', 'S', 'VP', 'ADVP', 'ADVP', 'RBR', 'more']]
than
[['S', 'S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'VP', 'NP', 'SBAR', 'S', 'VP', 'ADVP', 'PP', 'IN', 'than']]
Dudley,
[['S', 'S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'VP', 'NP', 'SB

[['S', 'S', 'VP', 'SBAR', 'S', 'VP', 'PP', 'NP', 'PP', 'NP', 'PP', 'NP', 'SBAR', 'S', 'VP', 'VP', 'VBG', 'swaying']]
darkly
[['S', 'S', 'VP', 'SBAR', 'S', 'VP', 'PP', 'NP', 'PP', 'NP', 'PP', 'NP', 'SBAR', 'S', 'VP', 'VP', 'ADVP', 'RB', 'darkly']]
in
[['S', 'S', 'VP', 'SBAR', 'S', 'VP', 'PP', 'NP', 'PP', 'NP', 'PP', 'NP', 'SBAR', 'S', 'VP', 'VP', 'PP', 'IN', 'in']]
the
[['S', 'S', 'VP', 'SBAR', 'S', 'VP', 'PP', 'NP', 'PP', 'NP', 'PP', 'NP', 'SBAR', 'S', 'VP', 'VP', 'PP', 'NP', 'DT', 'the']]
distance.
[['S', 'S', 'VP', 'SBAR', 'S', 'VP', 'PP', 'NP', 'PP', 'NP', 'PP', 'NP', 'SBAR', 'S', 'VP', 'VP', 'PP', 'NP', 'NN', 'distance'], ['S', '.', '.']]
+
[]
The
[['S', 'S', 'NP', 'DT', 'The']]
Slytherins
[['S', 'S', 'NP', 'NNPS', 'Slytherins']]
were
[['S', 'S', 'VP', 'VBD', 'were']]
already
[['S', 'S', 'VP', 'ADVP', 'RB', 'already']]
there,
[['S', 'S', 'VP', 'ADVP', 'RB', 'there'], ['S', ',', ',']]
and
[['S', 'CC', 'and']]
so
[['S', 'SINV', 'ADVP', 'RB', 'so']]
were
[['S', 'SINV', 'VP', 'VBD', 'w

[['S', 'S', 'S', 'VP', 'SBAR', 'S', 'VP', 'VP', 'NP', 'SBAR', 'S', 'VP', 'VP', 'PP', 'IN', 'without']]
being
[['S', 'S', 'S', 'VP', 'SBAR', 'S', 'VP', 'VP', 'NP', 'SBAR', 'S', 'VP', 'VP', 'PP', 'S', 'VP', 'VBG', 'being']]
taught
[['S', 'S', 'S', 'VP', 'SBAR', 'S', 'VP', 'VP', 'NP', 'SBAR', 'S', 'VP', 'VP', 'PP', 'S', 'VP', 'VP', 'VBN', 'taught']]
--
[['S', 'S', ':', '--']]
this
[['S', 'S', 'S', 'S', 'NP', 'DT', 'this']]
was
[['S', 'S', 'S', 'S', 'VP', 'VBD', 'was']]
easy,
[['S', 'S', 'S', 'S', 'VP', 'ADJP', 'JJ', 'easy'], ['S', 'S', 'S', ',', ',']]
this
[['S', 'S', 'S', 'S', 'NP', 'DT', 'this']]
was
[['S', 'S', 'S', 'S', 'VP', 'VBD', 'was']]
wonderful.
[['S', 'S', 'S', 'S', 'VP', 'ADJP', 'JJ', 'wonderful'], ['S', '.', '.']]
He
[['S', 'NP', 'PRP', 'He']]
pulled
[['S', 'VP', 'VP', 'VBD', 'pulled']]
his
[['S', 'VP', 'VP', 'NP', 'PRP$', 'his']]
broomstick
[['S', 'VP', 'VP', 'NP', 'NN', 'broomstick']]
up
[['S', 'VP', 'VP', 'ADVP', 'RP', 'up']]
a
[['S', 'VP', 'VP', 'NP', 'DT', 'a']]
little
[

imagined
[['S', 'VP', 'SBAR', 'S', 'VP', 'VBD', 'imagined']]
it,
[['S', 'VP', 'SBAR', 'S', 'VP', 'NP', 'PRP', 'it'], ['S', 'VP', ',', ',']]
watching
[['S', 'VP', 'S', 'VP', 'VBG', 'watching']]
Ron
[['S', 'VP', 'S', 'VP', 'S', 'NP', 'NP', 'NNP', 'Ron']]
and
[['S', 'VP', 'S', 'VP', 'S', 'NP', 'CC', 'and']]
the
[['S', 'VP', 'S', 'VP', 'S', 'NP', 'NP', 'DT', 'the']]
others
[['S', 'VP', 'S', 'VP', 'S', 'NP', 'NP', 'NNS', 'others']]
becoming
[['S', 'VP', 'S', 'VP', 'S', 'VP', 'VBG', 'becoming']]
wizards
[['S', 'VP', 'S', 'VP', 'S', 'VP', 'NP', 'NNS', 'wizards']]
while
[['S', 'VP', 'S', 'VP', 'S', 'VP', 'SBAR', 'IN', 'while']]
he
[['S', 'VP', 'S', 'VP', 'S', 'VP', 'SBAR', 'S', 'NP', 'PRP', 'he']]
stumped
[['S', 'VP', 'S', 'VP', 'S', 'VP', 'SBAR', 'S', 'VP', 'VBD', 'stumped']]
around
[['S', 'VP', 'S', 'VP', 'S', 'VP', 'SBAR', 'S', 'VP', 'PP', 'IN', 'around']]
the
[['S', 'VP', 'S', 'VP', 'S', 'VP', 'SBAR', 'S', 'VP', 'PP', 'NP', 'DT', 'the']]
grounds
[['S', 'VP', 'S', 'VP', 'S', 'VP', 'SBAR', '

[['S', 'S', 'VP', 'SBAR', 'S', 'VP', 'VP', 'NP', 'PP', 'PP', 'IN', 'of']]
the
[['S', 'S', 'VP', 'SBAR', 'S', 'VP', 'VP', 'NP', 'PP', 'PP', 'NP', 'DT', 'the']]
school."
[['S', 'S', 'VP', 'SBAR', 'S', 'VP', 'VP', 'NP', 'PP', 'PP', 'NP', 'NN', 'school'], ['S', '.', '.'], ['S', "''", "''"]]
+
[]
"Bet
[['S', '``', '``'], ['S', 'VP', 'VB', 'Bet']]
it's
[['S', 'VP', 'SBAR', 'S', 'NP', 'PRP', 'it'], ['S', 'VP', 'SBAR', 'S', 'VP', 'VBZ', "'s"]]
that
[['S', 'VP', 'SBAR', 'S', 'VP', 'NP', 'NP', 'DT', 'that']]
one
[['S', 'VP', 'SBAR', 'S', 'VP', 'NP', 'NP', 'CD', 'one']]
behind
[['S', 'VP', 'SBAR', 'S', 'VP', 'NP', 'PP', 'IN', 'behind']]
the
[['S', 'VP', 'SBAR', 'S', 'VP', 'NP', 'PP', 'NP', 'NP', 'DT', 'the']]
statue
[['S', 'VP', 'SBAR', 'S', 'VP', 'NP', 'PP', 'NP', 'NP', 'NN', 'statue']]
of
[['S', 'VP', 'SBAR', 'S', 'VP', 'NP', 'PP', 'NP', 'PP', 'IN', 'of']]
Gregory
[['S', 'VP', 'SBAR', 'S', 'VP', 'NP', 'PP', 'NP', 'PP', 'NP', 'NP', 'NNP', 'Gregory']]
the
[['S', 'VP', 'SBAR', 'S', 'VP', 'NP', 'PP

[['S', 'VP', 'VP', 'S', 'VP', 'PP', 'NP', 'NNS', 'shadows'], ['S', '.', '.']]
They
[['S', 'NP', 'PRP', 'They']]
had
[['S', 'VP', 'VBD', 'had']]
almost
[['S', 'VP', 'ADVP', 'RB', 'almost']]
reached
[['S', 'VP', 'VP', 'VBN', 'reached']]
the
[['S', 'VP', 'VP', 'NP', 'DT', 'the']]
portrait
[['S', 'VP', 'VP', 'NP', 'NN', 'portrait']]
hole
[['S', 'VP', 'VP', 'NP', 'NN', 'hole']]
when
[['S', 'VP', 'VP', 'SBAR', 'WHADVP', 'WRB', 'when']]
a
[['S', 'VP', 'VP', 'SBAR', 'S', 'NP', 'DT', 'a']]
voice
[['S', 'VP', 'VP', 'SBAR', 'S', 'NP', 'NN', 'voice']]
spoke
[['S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'VBD', 'spoke']]
from
[['S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'PP', 'IN', 'from']]
the
[['S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'PP', 'NP', 'NP', 'DT', 'the']]
chair
[['S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'PP', 'NP', 'NP', 'NN', 'chair']]
nearest
[['S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'PP', 'NP', 'PP', 'JJS', 'nearest']]
them,
[['S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'PP', 'NP', 'PP', 'NP', 'PRP', 'them'], ['S', 'VP'

the
[['S', 'S', 'VP', 'PP', 'NP', 'DT', 'the']]
door,
[['S', 'S', 'VP', 'PP', 'NP', 'NN', 'door'], ['S', 'S', 'VP', ',', ',']]
away
[['S', 'S', 'VP', 'ADVP', 'RB', 'away']]
from
[['S', 'S', 'VP', 'ADVP', 'PP', 'IN', 'from']]
Filch's
[['S', 'S', 'VP', 'ADVP', 'PP', 'NP', 'NP', 'NNP', 'Filch'], ['S', 'S', 'VP', 'ADVP', 'PP', 'NP', 'NP', 'POS', "'s"]]
voice.
[['S', 'S', 'VP', 'ADVP', 'PP', 'NP', 'NN', 'voice'], ['S', '.', '.']]
Neville's
[['S', 'NP', 'NP', 'NNP', 'Neville'], ['S', 'NP', 'NP', 'POS', "'s"]]
robes
[['S', 'NP', 'NNS', 'robes']]
had
[['S', 'VP', 'VBD', 'had']]
barely
[['S', 'VP', 'ADVP', 'RB', 'barely']]
whipped
[['S', 'VP', 'VP', 'VBN', 'whipped']]
round
[['S', 'VP', 'VP', 'PP', 'IN', 'round']]
the
[['S', 'VP', 'VP', 'PP', 'NP', 'DT', 'the']]
corner
[['S', 'VP', 'VP', 'PP', 'NP', 'NN', 'corner']]
when
[['S', 'VP', 'VP', 'SBAR', 'WHADVP', 'WRB', 'when']]
they
[['S', 'VP', 'VP', 'SBAR', 'S', 'NP', 'PRP', 'they']]
heard
[['S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'VBD', 'heard']]
Fil

"Don't
[['SBARQ', '``', '``'], ['SBARQ', 'VBP', 'Do'], ['SBARQ', 'RB', "n't"]]
mess
[['SBARQ', 'VP', 'VP', 'VB', 'mess']]
with
[['SBARQ', 'VP', 'VP', 'PP', 'IN', 'with']]
me,
[['SBARQ', 'VP', 'VP', 'PP', 'NP', 'PRP', 'me'], ['SBARQ', 'VP', ',', ',']]
Peeves,
[['SBARQ', 'VP', 'NP', 'NNS', 'Peeves'], ['SBARQ', ',', ',']]
now
[['SBARQ', 'ADVP', 'RB', 'now']]
where
[['SBARQ', 'WHADVP', 'WRB', 'where']]
did
[['SBARQ', 'SQ', 'VBD', 'did']]
they
[['SBARQ', 'SQ', 'NP', 'PRP', 'they']]
go?"
[['SBARQ', 'SQ', 'VP', 'VB', 'go'], ['SBARQ', '.', '?'], ['SBARQ', "''", "''"]]
"Shan't
[['SINV', '``', '``'], ['SINV', 'S', 'VP', 'MD', 'Sha'], ['SINV', 'S', 'VP', 'RB', "n't"]]
say
[['SINV', 'S', 'VP', 'VP', 'VB', 'say']]
nothing
[['SINV', 'S', 'VP', 'VP', 'NP', 'NN', 'nothing']]
if
[['SINV', 'S', 'VP', 'VP', 'SBAR', 'IN', 'if']]
you
[['SINV', 'S', 'VP', 'VP', 'SBAR', 'S', 'NP', 'PRP', 'you']]
don't
[['SINV', 'S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'VBP', 'do'], ['SINV', 'S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'RB

have
[['S', 'VP', 'VP', 'VB', 'have']]
been
[['S', 'VP', 'VP', 'VP', 'VBN', 'been']]
killed
[['S', 'VP', 'VP', 'VP', 'VP', 'VP', 'VBN', 'killed']]
--
[['S', 'VP', 'VP', 'VP', 'VP', ':', '--']]
or
[['S', 'VP', 'VP', 'VP', 'VP', 'CC', 'or']]
worse,
[['S', 'VP', 'VP', 'VP', 'VP', 'ADVP', 'JJR', 'worse'], ['S', 'VP', 'VP', 'VP', 'VP', ',', ',']]
expelled.
[['S', 'VP', 'VP', 'VP', 'VP', 'VP', 'VBN', 'expelled'], ['S', '.', '.']]
Now,
[['S', 'ADVP', 'RB', 'Now'], ['S', ',', ',']]
if
[['S', 'SBAR', 'IN', 'if']]
you
[['S', 'SBAR', 'S', 'NP', 'PRP', 'you']]
don't
[['S', 'SBAR', 'S', 'VP', 'VBP', 'do'], ['S', 'SBAR', 'S', 'VP', 'RB', "n't"]]
mind,
[['S', 'SBAR', 'S', 'VP', 'VP', 'VB', 'mind'], ['S', ',', ',']]
I'm
[['S', 'NP', 'PRP', 'I'], ['S', 'VP', 'VBP', "'m"]]
going
[['S', 'VP', 'VP', 'VBG', 'going']]
to
[['S', 'VP', 'VP', 'PP', 'TO', 'to']]
bed."
[['S', 'VP', 'VP', 'PP', 'NP', 'VB', 'bed'], ['S', '.', '.'], ['S', "''", "''"]]
+
[]
Ron
[['S', 'NP', 'NNP', 'Ron']]
stared
[['S', 'VP', 'VBD', 

In [9]:
print(max_path_len) # number of levels = max path len from root to any leaf
print(tag_to_idx)

21
{'S': 0, 'NP': 1, 'NNP': 2, 'VP': 3, 'VBD': 4, 'ADVP': 5, 'RB': 6, 'VBN': 7, 'SBAR': 8, 'PRP': 9, 'MD': 10, 'VB': 11, 'DT': 12, 'NN': 13, 'RBR': 14, 'PP': 15, 'IN': 16, ',': 17, 'CC': 18, '.': 19, 'JJ': 20, 'NNS': 21, 'NNPS': 22, 'TO': 23, 'PRT': 24, 'RP': 25, 'JJS': 26, 'WHNP': 27, 'WDT': 28, 'VBG': 29, ':': 30, 'SINV': 31, '``': 32, 'ADJP': 33, "''": 34, 'FRAG': 35, 'WP': 36, 'VBP': 37, 'VBZ': 38, 'WHADJP': 39, 'WRB': 40, 'PRP$': 41, 'POS': 42, 'QP': 43, 'CD': 44, 'WHADVP': 45, 'EX': 46, 'UH': 47, 'SBARQ': 48, 'SQ': 49, 'WP$': 50, 'INTJ': 51, 'PRN': 52, 'UCP': 53, 'JJR': 54, 'PDT': 55, '-LRB-': 56, '-RRB-': 57, 'FW': 58}


In [10]:
import numpy as np
import os

noun_phrase = ["NP", "WHNP"]
verb_phrase = ["VP"]
adverb_phrase = ["ADVP", "WHAVP"]
adjective_phrase = ["ADJP", "WHADJP"]
prepositional_phrase = ["PP", "WHPP"]
clauses = ["S", "SBAR", "SBARQ", "SINV", "SQ"]

for ancestor_level in range(2,10):
    labels = np.zeros((len(hp_text), 7))
    for i in range(len(hp_text)):
        t = []
        paths = all_paths[i]
        for j in range(len(paths)):    
            t.append(paths[j][-min(ancestor_level+1,len(paths[j]))])
        
        classes = []
        for tag in t:
            if tag in noun_phrase:
                labels[i, 0] = 1
                classes.append("Noun Phrase")
            elif tag in verb_phrase:
                labels[i, 1] = 1
                classes.append("Verb Phrase")
            elif tag in adverb_phrase:
                labels[i, 2] = 1
                classes.append("Adverb Phrase")
            elif tag in adjective_phrase:
                labels[i, 3] = 1
                classes.append("Adjective Phrase")
            elif tag in prepositional_phrase:
                labels[i, 4] = 1
                classes.append("Prepositional Phrase")
            elif tag in clauses:
                labels[i, 5] = 1
                classes.append("Clauses")
            else:
                labels[i, 6] = 1
                classes.append("Miscellaneous")
        
        print("Ancestors at level {} for {} are {} which belong to buckets {}".format(ancestor_level, hp_text[i], t, classes))
        print("Paths to the root for this word are {}\n".format(all_paths[i]))
        
    np.save("{}/level_{}_ancestors".format(save_dir, ancestor_level), labels)

Ancestors at level 2 for Harry are ['NP'] which belong to buckets ['Noun Phrase']
Paths to the root for this word are [['S', 'S', 'NP', 'NNP', 'Harry']]

Ancestors at level 2 for had are ['VP'] which belong to buckets ['Verb Phrase']
Paths to the root for this word are [['S', 'S', 'VP', 'VBD', 'had']]

Ancestors at level 2 for never are ['ADVP'] which belong to buckets ['Adverb Phrase']
Paths to the root for this word are [['S', 'S', 'VP', 'ADVP', 'RB', 'never']]

Ancestors at level 2 for believed are ['VP'] which belong to buckets ['Verb Phrase']
Paths to the root for this word are [['S', 'S', 'VP', 'VP', 'VBN', 'believed']]

Ancestors at level 2 for he are ['NP'] which belong to buckets ['Noun Phrase']
Paths to the root for this word are [['S', 'S', 'VP', 'VP', 'SBAR', 'S', 'NP', 'PRP', 'he']]

Ancestors at level 2 for would are ['VP'] which belong to buckets ['Verb Phrase']
Paths to the root for this word are [['S', 'S', 'VP', 'VP', 'SBAR', 'S', 'VP', 'MD', 'would']]

Ancestors at l

Paths to the root for this word are [['S', 'VP', 'VP', 'S', 'VP', 'NP', 'PP', 'NP', 'NNP', 'Ham']]

Ancestors at level 2 for soccer are ['NP'] which belong to buckets ['Noun Phrase']
Paths to the root for this word are [['S', 'VP', 'VP', 'S', 'VP', 'NP', 'PP', 'NP', 'NN', 'soccer']]

Ancestors at level 2 for team, are ['NP', 'S'] which belong to buckets ['Noun Phrase', 'Clauses']
Paths to the root for this word are [['S', 'VP', 'VP', 'S', 'VP', 'NP', 'PP', 'NP', 'NN', 'team'], ['S', 'VP', 'VP', 'S', ',', ',']]

Ancestors at level 2 for trying are ['VP'] which belong to buckets ['Verb Phrase']
Paths to the root for this word are [['S', 'VP', 'VP', 'S', 'S', 'VP', 'VBG', 'trying']]

Ancestors at level 2 for to are ['VP'] which belong to buckets ['Verb Phrase']
Paths to the root for this word are [['S', 'VP', 'VP', 'S', 'S', 'VP', 'S', 'VP', 'TO', 'to']]

Ancestors at level 2 for make are ['VP'] which belong to buckets ['Verb Phrase']
Paths to the root for this word are [['S', 'VP', 'VP',

Paths to the root for this word are [['S', 'VP', 'VP', 'NP', 'CC', 'and']]

Ancestors at level 2 for George are ['NP'] which belong to buckets ['Noun Phrase']
Paths to the root for this word are [['S', 'VP', 'VP', 'NP', 'NP', 'NNP', 'George']]

Ancestors at level 2 for Weasley are ['NP'] which belong to buckets ['Noun Phrase']
Paths to the root for this word are [['S', 'VP', 'VP', 'NP', 'NP', 'NNP', 'Weasley']]

Ancestors at level 2 for complain are ['VP'] which belong to buckets ['Verb Phrase']
Paths to the root for this word are [['S', 'VP', 'VP', 'VP', 'VB', 'complain']]

Ancestors at level 2 for about are ['PP'] which belong to buckets ['Prepositional Phrase']
Paths to the root for this word are [['S', 'VP', 'VP', 'VP', 'PP', 'IN', 'about']]

Ancestors at level 2 for the are ['NP'] which belong to buckets ['Noun Phrase']
Paths to the root for this word are [['S', 'VP', 'VP', 'VP', 'PP', 'NP', 'DT', 'the']]

Ancestors at level 2 for school are ['NP'] which belong to buckets ['Noun P


Ancestors at level 2 for "Broken are ['S', 'NP'] which belong to buckets ['Clauses', 'Noun Phrase']
Paths to the root for this word are [['S', '``', '``'], ['S', 'FRAG', 'NP', 'VBN', 'Broken']]

Ancestors at level 2 for wrist," are ['NP', 'S', 'S'] which belong to buckets ['Noun Phrase', 'Clauses', 'Clauses']
Paths to the root for this word are [['S', 'FRAG', 'NP', 'NN', 'wrist'], ['S', ',', ','], ['S', "''", "''"]]

Ancestors at level 2 for Harry are ['NP'] which belong to buckets ['Noun Phrase']
Paths to the root for this word are [['S', 'NP', 'NNP', 'Harry']]

Ancestors at level 2 for heard are ['VP'] which belong to buckets ['Verb Phrase']
Paths to the root for this word are [['S', 'VP', 'VBD', 'heard']]

Ancestors at level 2 for her are ['NP'] which belong to buckets ['Noun Phrase']
Paths to the root for this word are [['S', 'VP', 'S', 'NP', 'PRP', 'her']]

Ancestors at level 2 for mutter. are ['VP', 'S'] which belong to buckets ['Verb Phrase', 'Clauses']
Paths to the root for th

Paths to the root for this word are [['S', 'VP', 'NP', 'NP', 'NN', 'thing']]

Ancestors at level 2 for Longbottom's are ['NP', 'NP'] which belong to buckets ['Noun Phrase', 'Noun Phrase']
Paths to the root for this word are [['S', 'VP', 'NP', 'SBAR', 'S', 'NP', 'NP', 'NNP', 'Longbottom'], ['S', 'VP', 'NP', 'SBAR', 'S', 'NP', 'NP', 'POS', "'s"]]

Ancestors at level 2 for gran are ['NP'] which belong to buckets ['Noun Phrase']
Paths to the root for this word are [['S', 'VP', 'NP', 'SBAR', 'S', 'NP', 'NN', 'gran']]

Ancestors at level 2 for sent are ['VP'] which belong to buckets ['Verb Phrase']
Paths to the root for this word are [['S', 'VP', 'NP', 'SBAR', 'S', 'VP', 'VBD', 'sent']]

Ancestors at level 2 for him." are ['NP', 'S', 'S'] which belong to buckets ['Noun Phrase', 'Clauses', 'Clauses']
Paths to the root for this word are [['S', 'VP', 'NP', 'SBAR', 'S', 'VP', 'NP', 'PRP', 'him'], ['S', '.', '.'], ['S', "''", "''"]]

Ancestors at level 2 for + are [] which belong to buckets []
Pa

...

Ancestors at level 9 for his are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'VP', 'NP', 'PRP$', 'his']]

Ancestors at level 9 for fault, are ['S', 'S'] which belong to buckets ['Clauses', 'Clauses']
Paths to the root for this word are [['S', 'VP', 'NP', 'NN', 'fault'], ['S', 'VP', ',', ',']]

Ancestors at level 9 for Professor are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'VP', 'NP', 'NN', 'Professor']]

Ancestors at level 9 for --" are ['S', 'S'] which belong to buckets ['Clauses', 'Clauses']
Paths to the root for this word are [['S', ':', '--'], ['S', "''", "''"]]

Ancestors at level 9 for + are [] which belong to buckets []
Paths to the root for this word are []

Ancestors at level 9 for "Be are ['S', 'S'] which belong to buckets ['Clauses', 'Clauses']
Paths to the root for this word are [['S', '``', '``'], ['S', 'VB', 'Be']]

Ancestors at level 9 for quiet, are ['S', 'S'] which belong to buckets ['


Ancestors at level 9 for dinnertime. are ['S', 'S'] which belong to buckets ['Clauses', 'Clauses']
Paths to the root for this word are [['S', 'VP', 'NP', 'NN', 'dinnertime'], ['S', '.', '.']]

Ancestors at level 9 for Harry are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'NP', 'NNP', 'Harry']]

Ancestors at level 9 for had are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'VP', 'VBD', 'had']]

Ancestors at level 9 for just are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'VP', 'ADVP', 'RB', 'just']]

Ancestors at level 9 for finished are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'VP', 'VP', 'VBN', 'finished']]

Ancestors at level 9 for telling are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'VP', 'VP', 'S', 'VP', 'VBG', 'telling']]

Ancestors at level 9 for Ron are ['S'] which belong 

Paths to the root for this word are [['S', 'VP', 'VP', 'SBAR', 'S', 'S', 'NP', 'PRP', 'I']]

Ancestors at level 9 for was are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'VP', 'VP', 'SBAR', 'S', 'S', 'VP', 'VBD', 'was']]

Ancestors at level 9 for trying are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'VP', 'VP', 'SBAR', 'S', 'S', 'VP', 'VP', 'VBG', 'trying']]

Ancestors at level 9 for to are ['VP'] which belong to buckets ['Verb Phrase']
Paths to the root for this word are [['S', 'VP', 'VP', 'SBAR', 'S', 'S', 'VP', 'VP', 'S', 'VP', 'TO', 'to']]

Ancestors at level 9 for stop are ['SBAR'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'VP', 'VP', 'SBAR', 'S', 'S', 'VP', 'VP', 'S', 'VP', 'VP', 'VB', 'stop']]

Ancestors at level 9 for you, are ['S', 'S'] which belong to buckets ['Clauses', 'Clauses']
Paths to the root for this word are [['S', 'VP', 'VP', 'SBAR', 'S', 'S', 'VP'

Ancestors at level 9 for "Say are ['S', 'S'] which belong to buckets ['Clauses', 'Clauses']
Paths to the root for this word are [['S', '``', '``'], ['S', 'VP', 'VB', 'Say']]

Ancestors at level 9 for 'please.'" are ['S', 'S', 'S', 'S'] which belong to buckets ['Clauses', 'Clauses', 'Clauses', 'Clauses']
Paths to the root for this word are [['S', 'VP', 'INTJ', 'UH', "'please"], ['S', '.', '.'], ['S', "''", "'"], ['S', "''", "''"]]

Ancestors at level 9 for + are [] which belong to buckets []
Paths to the root for this word are []

Ancestors at level 9 for "Don't are ['SBARQ', 'SBARQ', 'SBARQ'] which belong to buckets ['Clauses', 'Clauses', 'Clauses']
Paths to the root for this word are [['SBARQ', '``', '``'], ['SBARQ', 'VBP', 'Do'], ['SBARQ', 'RB', "n't"]]

Ancestors at level 9 for mess are ['SBARQ'] which belong to buckets ['Clauses']
Paths to the root for this word are [['SBARQ', 'VP', 'VP', 'VB', 'mess']]

Ancestors at level 9 for with are ['SBARQ'] which belong to buckets ['Clauses'

Ancestors at level 9 for pleased are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'VP', 'SBAR', 'S', 'VP', 'ADJP', 'JJ', 'pleased']]

Ancestors at level 9 for with are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'VP', 'SBAR', 'S', 'VP', 'ADJP', 'PP', 'IN', 'with']]

Ancestors at level 9 for yourselves. are ['S', 'S'] which belong to buckets ['Clauses', 'Clauses']
Paths to the root for this word are [['S', 'VP', 'SBAR', 'S', 'VP', 'ADJP', 'PP', 'NP', 'PRP', 'yourselves'], ['S', '.', '.']]

Ancestors at level 9 for We are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'NP', 'PRP', 'We']]

Ancestors at level 9 for could are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'VP', 'MD', 'could']]

Ancestors at level 9 for all are ['S'] which belong to buckets ['Clauses']
Paths to the root for this word are [['S', 'VP', 'DT', 'all']]

Ances